### Open WRF output file and read some variables

In [ ]:
import numpy, Nio, Ngl, os

filename = "wrfout_d03_2012-04-22_23_00_00.nc"
f  = Nio.open_file(filename,"r")          # Open WRF output file
T  = f.variables["T"]                     # potential temperature
P  = f.variables["P"]                     # perturbation pressure
PB = f.variables["PB"]                    # base pressure
print T
print P
print PB

### Calculate temperature from T, P, PB using "wrf_tk" function

In [ ]:
THETA = T[:]+300          # perturbation + reference temperature
PPB   = P[:] + PB[:]
TK   = Ngl.wrf_tk(PPB, THETA)

print "TK min/max = %g / %g" % (numpy.min(TK[:]),numpy.max(TK[:]))

# Write TK to new NetCDF file

### Open file for creation

In [ ]:
out_filename = "wrfout_new.nc"
if(os.path.exists(out_filename)):
    os.remove(out_filename)
fout = Nio.open_file(out_filename,"c")

### Add some global attributes to file

In [ ]:
fout.history       = "File created as a demo at SEA2015"
fout.creation_date = os.system("date")

### Add dimensions to file based on T's dimensions

In [ ]:
print T.dimensions
print T.shape
for idim in range(len(T.dimensions)):
    fout.create_dimension(T.dimensions[idim],T.shape[idim])

### Define variable on file

In [ ]:
new_var_name = "TK"
fout.create_variable(new_var_name,'d',T.dimensions)

### Write attributes of variable to file, changing "description" and "units"

In [ ]:
varAtts = T.__dict__.keys()    # Get all of T's attributes
varAtts.sort()
for att in varAtts:
    if att is "description":
        value = "Temperature"
    elif att is "units":
        value = "degK"      # Better than just "K"
    else:
        value = getattr(T,att)
        
    setattr(fout.variables[new_var_name],att,value)   # Write attribute and value to file

### Write data values to file and close it

In [ ]:
fout.variables[new_var_name].assign_value(TK)
fout.close()

### Reopen file and print it

In [ ]:
f = Nio.open_file(out_filename,"r")
print f

### Read TK

In [ ]:
tk = f.variables["TK"]
print "TK after reading back in: %g / %g" % (numpy.min(tk[:]),numpy.max(tk[:]))
print TK.shape

### Plot TK

In [ ]:
from wrf_plot_ngl import *
wrf_plot_var(tk[0,0,:,:],contour_type="raster",title="TK")

from IPython.display import Image
Image(filename='wrfplot.png')